In [1]:
import pytz
import datetime
import pandas as pd
import collections
import re
from pymongo import MongoClient
import numpy as np

ModuleNotFoundError: No module named 'pymongo'

In [2]:
def removeSpecialCharacters(value):
    return re.sub('[^A-Za-z0-9]+', ' ', str(value))

def cleanDataColumns(data):
    trueCol = []
    for col in data.columns:
        trueCol.append(removeSpecialCharacters(col))
    data.columns = trueCol
    return data

def limpa_cpf(cpfString):
    cpfString = cpfString.replace('.','')
    cpfString = cpfString.replace('-','')
    return int(cpfString)    

def limpeza_de_cpfs(dados, coluna):
    dados[coluna] = dados.loc[:,coluna].apply(limpa_cpf)
    return dados
    
def coluna_para_datetime(data, coluna):
    print('NECESSARIO UMA PROTECAO AQUI PARA CORRIGIR PROBLEMAS NOS DADOS')
    data[coluna] = pd.to_datetime(data[coluna], format='%d/%m/%Y')
    data[coluna] = data.loc[:,coluna].apply(date_to_Brazil_East_Utc)
    return data

def date_to_Brazil_East_Utc(datetime_value): # ele adianta o relogio em 3 horas
    local = pytz.timezone("Brazil/East")
    local_dt = local.localize(datetime_value, is_dst=None)
    utc_dt = local_dt.astimezone(pytz.utc)
    return utc_dt.strftime ("%Y-%m-%d %H:%M:%S")

def float_latin_nan_e_zero(entry):
    if _isNan(entry):
        return 0.0e0
    else:
        return floatLatin(entry)
    

def floatLatin(entry):
    if _isNan(entry):
        return np.nan
    entry = str(entry).replace('.','')
    entry = str(entry).replace(',','.')
    return float(entry)

def _isNan(value):
    if isinstance(value, str):
        return value == 'nan'
    else:
        return np.isnan(value)


# TRANSFORMACOES ESPECIFICAS DA TABELA ACORDOS

def transforma_Assessoria(valor):
    if str(valor) == 'nan':
        return 'SEMEAR'
    else:
        return str(valor)

def transforma_Cobrador(valor):
    if 'Semear_Renego' in valor:
        return 'Renegociacao'
    elif 'Multiparcelas' in valor:
        return 'Multiparcelas'
    else:
        return 'NULO'

# TRANSFORMACOES ESPECIFICAS DA TABELA ACIONAMENTOS

def coluna_para_datetime_hora(data, coluna):
    print('NECESSARIO UMA PROTECAO AQUI PARA CORRIGIR PROBLEMAS NOS DADOS')
    data[coluna] = pd.to_datetime(data[coluna], format='%d/%m/%Y %H:%M')
    data[coluna] = data.loc[:,coluna].apply(date_to_Brazil_East_Utc)
    return data


# Leitura dos dados

In [3]:
dados = pd.read_csv('Acionamentos_01012019_a_30062019.csv', sep=';', encoding='latin-1', dtype=str)

In [4]:
dados = cleanDataColumns(dados)

In [5]:
# Se o CPF for null e pra dropar.
cpf_null = dados[dados.loc[:,'CPF CNPJ'].isnull()].index
dados = dados.drop(cpf_null)
dados = dados.reset_index(drop=True)

In [ ]:
# Criacao da coluna datahora
datahora = []
for i in dados.index:
    datahora.append(dados.loc[i,'Data'] + ' ' + dados.loc[i,'Hor rio'])
dados['datahora'] = datahora
dados = coluna_para_datetime_hora(dados, 'datahora')

In [6]:
dados = limpeza_de_cpfs(dados, 'CPF CNPJ')

In [ ]:
responsaveis = collections.Counter(dados.loc[:,'Respons vel']).most_common() 
# lista os nomes de responsaveis do semear pela ligacao telefonica
# Com o nome dos responsaveis eu crio um ID para cada funcionario do Semear.
# Depois e necessario criar uma variavel que coloca o responsavel por ID, se nao tiver coloca a agencia que fez a cobranca

In [63]:
#Criacao de ids
# Responsavel_ID
Responsavel_ID = {}
k = 0
for ires in responsaveis:
    if ires[1] == 138067: # neste contexto, o nan significa que a ligação foi feita pela assessoria
        continue
    nome_limpo = removeSpecialCharacters(ires[0])
    Responsavel_ID[nome_limpo] = 'Semear_' + str(k)
    k += 1
responsaveis_acionamentos = {
    'Responsaveis': 'Relatorio_de_acionamentos',
    'Responsaveis_ID': Responsavel_ID   
}

In [78]:
responsaveis_pelo_acionamento = []
for i in dados.index:
    responsavel = removeSpecialCharacters(dados.loc[i,'Respons vel'])
    if responsavel == 'nan':
        responsavel = dados.loc[i,'Assessoria']
    else:
        responsavel = Responsavel_ID[responsavel]
    responsaveis_pelo_acionamento.append(responsavel)
dados['responsavel_pelo_acionamento'] = responsaveis_pelo_acionamento

# TRABALHANDO AQUI PARA DAR CARGA NO DATA POOL

In [84]:
ligacao_telefonica_ID = 0
for i in dados.index:
    ligacao_telefonica_ID += 1
    dados_dict = {'ligacao_telefonica_ID': ligacao_telefonica_ID,
                    'Numero_do_CPF': int(dados.loc[i,'CPF CNPJ']),
                  'Data_hora_da_ligacao': dados.loc[i,'datahora'],
                  'Responsavel_pela_ligacao':dados.loc[i,'responsavel_pelo_acionamento'],
                  'Motivo_da_ligacao': str(dados.loc[i,'Motivo Contato']),
                  'Dias_em_atraso_na_data_da_ligacao': int(dados.loc[i,'Dias atraso'])
                 }
    if i > 10:
        break
    print(dados_dict)

{'ligacao_telefonica_ID': 1, 'Numero_do_CPF': 62361643120, 'Data_hora_da_ligacao': '2019-02-19 15:46:00', 'Responsavel_pela_ligacao': 'Semear_3', 'Motivo_da_ligacao': 'CONTRA PROPOSTA', 'Dias_em_atraso_na_data_da_ligacao': 104}
{'ligacao_telefonica_ID': 2, 'Numero_do_CPF': 97766330130, 'Data_hora_da_ligacao': '2019-02-19 15:53:00', 'Responsavel_pela_ligacao': 'Semear_3', 'Motivo_da_ligacao': 'CONTRA PROPOSTA', 'Dias_em_atraso_na_data_da_ligacao': 315}
{'ligacao_telefonica_ID': 3, 'Numero_do_CPF': 64756394604, 'Data_hora_da_ligacao': '2019-02-20 16:18:00', 'Responsavel_pela_ligacao': 'Semear_3', 'Motivo_da_ligacao': 'CONTRA PROPOSTA', 'Dias_em_atraso_na_data_da_ligacao': 203}
{'ligacao_telefonica_ID': 4, 'Numero_do_CPF': 13309848620, 'Data_hora_da_ligacao': '2019-02-20 16:20:00', 'Responsavel_pela_ligacao': 'Semear_3', 'Motivo_da_ligacao': 'CONTRA PROPOSTA', 'Dias_em_atraso_na_data_da_ligacao': 245}
{'ligacao_telefonica_ID': 5, 'Numero_do_CPF': 9557109602, 'Data_hora_da_ligacao': '2019-

# Definicao da coluna ligacoes_telefonicas

In [114]:
client = MongoClient()
client = MongoClient('localhost', 27017)
db = client.cobrancas
ligacoes_telefonicas = db.ligacoes_telefonicas

# Carga no banco de dados

In [86]:
ligacao_telefonica_ID = 0
for i in dados.index:
    ligacao_telefonica_ID += 1
    dados_dict = {'ligacao_telefonica_ID': ligacao_telefonica_ID,
                    'Numero_do_CPF': int(dados.loc[i,'CPF CNPJ']),
                  'Data_hora_da_ligacao': dados.loc[i,'datahora'],
                  'Responsavel_pela_ligacao':dados.loc[i,'responsavel_pelo_acionamento'],
                  'Motivo_da_ligacao': str(dados.loc[i,'Motivo Contato']),
                  'Dias_em_atraso_na_data_da_ligacao': int(dados.loc[i,'Dias atraso'])
                 }
    ligacoes_telefonicas.insert_one(dados_dict)

# Carga na informacao que relaciona o nome do funcionario Semear com sua Semear_ID.

In [107]:
informacoes_adicionais = db.informacoes_adicionais

In [108]:
informacoes_adicionais.insert_one(responsaveis_acionamentos)

# Todos os registros para um dado CPF

In [94]:
import pprint
cursor = ligacoes_telefonicas.find({'Numero_do_CPF': 42251262857})
for document in cursor:
    pprint.pprint(document)

{'Data_hora_da_ligacao': '2019-02-22 16:14:00',
 'Dias_em_atraso_na_data_da_ligacao': 1201,
 'Motivo_da_ligacao': 'CONTRA PROPOSTA',
 'Numero_do_CPF': 42251262857,
 'Responsavel_pela_ligacao': 'Semear_3',
 '_id': ObjectId('5d406c9fcdf51618d43a95c2'),
 'ligacao_telefonica_ID': 9}
{'Data_hora_da_ligacao': '2019-02-27 13:42:00',
 'Dias_em_atraso_na_data_da_ligacao': 1201,
 'Motivo_da_ligacao': 'CONTRA PROPOSTA',
 'Numero_do_CPF': 42251262857,
 'Responsavel_pela_ligacao': 'Semear_3',
 '_id': ObjectId('5d406c9fcdf51618d43a95cb'),
 'ligacao_telefonica_ID': 18}


# Todos os registros em um determinado intervalo de datas

In [123]:
start = date_to_Brazil_East_Utc(datetime.datetime(2019, 5, 3))
end = date_to_Brazil_East_Utc(datetime.datetime(2019, 6, 3))
query_datas_limite = {'Data_hora_da_ligacao': {'$lt': end, '$gte': start}}
cursor = ligacoes_telefonicas.find(query_datas_limite)
for document in cursor:
    print(document)

{'_id': ObjectId('5d406ccbcdf51618d43b4598'), 'ligacao_telefonica_ID': 45023, 'Numero_do_CPF': 97385824234, 'Data_hora_da_ligacao': '2019-05-03 10:25:00', 'Responsavel_pela_ligacao': 'Semear_0', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': -20}
{'_id': ObjectId('5d406ccbcdf51618d43b4599'), 'ligacao_telefonica_ID': 45024, 'Numero_do_CPF': 1310271151, 'Data_hora_da_ligacao': '2019-05-03 11:01:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 960}
{'_id': ObjectId('5d406ccbcdf51618d43b459a'), 'ligacao_telefonica_ID': 45025, 'Numero_do_CPF': 3780407663, 'Data_hora_da_ligacao': '2019-05-03 11:02:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 1509}
{'_id': ObjectId('5d406ccbcdf51618d43b459b'), 'ligacao_telefonica_ID': 45026, 'Numero_do_CPF': 10669911623, 'Data_hora_da_ligacao': '2019-05-03 11:04:00', 'Responsavel_

{'_id': ObjectId('5d406ccbcdf51618d43b45fd'), 'ligacao_telefonica_ID': 45124, 'Numero_do_CPF': 11132150620, 'Data_hora_da_ligacao': '2019-05-03 11:34:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM CARNE', 'Dias_em_atraso_na_data_da_ligacao': 101}
{'_id': ObjectId('5d406ccbcdf51618d43b45fe'), 'ligacao_telefonica_ID': 45125, 'Numero_do_CPF': 2417309106, 'Data_hora_da_ligacao': '2019-05-03 11:34:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'INTERESSE EM PAGAR', 'Dias_em_atraso_na_data_da_ligacao': 990}
{'_id': ObjectId('5d406ccbcdf51618d43b45ff'), 'ligacao_telefonica_ID': 45126, 'Numero_do_CPF': 63401118153, 'Data_hora_da_ligacao': '2019-05-03 11:35:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 2}
{'_id': ObjectId('5d406ccbcdf51618d43b4600'), 'ligacao_telefonica_ID': 45127, 'Numero_do_CPF': 83782427149, 'Data_hora_da_ligacao': '2019-05-03 11:35:00', 'Responsavel

{'_id': ObjectId('5d406ccdcdf51618d43b4e02'), 'ligacao_telefonica_ID': 47177, 'Numero_do_CPF': 14696887782, 'Data_hora_da_ligacao': '2019-05-06 12:00:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': 0}
{'_id': ObjectId('5d406ccdcdf51618d43b4e03'), 'ligacao_telefonica_ID': 47178, 'Numero_do_CPF': 54009332115, 'Data_hora_da_ligacao': '2019-05-06 12:00:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': 156}
{'_id': ObjectId('5d406ccdcdf51618d43b4e04'), 'ligacao_telefonica_ID': 47179, 'Numero_do_CPF': 7540149671, 'Data_hora_da_ligacao': '2019-05-06 12:00:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': 21}
{'_id': ObjectId('5d406ccdcdf51618d43b4e05'), 'ligacao_telefonica_ID': 47180, 'Numero_do_CPF': 48861804691, 'Data_hora_da_ligacao': '2019-05-06 12:01:00', 'Respo

{'_id': ObjectId('5d406ccecdf51618d43b51f2'), 'ligacao_telefonica_ID': 48185, 'Numero_do_CPF': 3270097646, 'Data_hora_da_ligacao': '2019-05-06 17:14:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 6}
{'_id': ObjectId('5d406ccecdf51618d43b51f3'), 'ligacao_telefonica_ID': 48186, 'Numero_do_CPF': 56322666649, 'Data_hora_da_ligacao': '2019-05-06 17:15:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 104}
{'_id': ObjectId('5d406ccecdf51618d43b51f4'), 'ligacao_telefonica_ID': 48187, 'Numero_do_CPF': 40425290620, 'Data_hora_da_ligacao': '2019-05-06 17:15:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 74}
{'_id': ObjectId('5d406ccecdf51618d43b51f5'), 'ligacao_telefonica_ID': 48188, 'Numero_do_CPF': 58023305620, 'Data_hora_da_ligacao': '2019-05-06 17:15:00', 'Responsavel_pela_lig

{'_id': ObjectId('5d406cd0cdf51618d43b57ce'), 'ligacao_telefonica_ID': 49685, 'Numero_do_CPF': 9018500631, 'Data_hora_da_ligacao': '2019-05-07 18:42:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 398}
{'_id': ObjectId('5d406cd0cdf51618d43b57cf'), 'ligacao_telefonica_ID': 49686, 'Numero_do_CPF': 8264555659, 'Data_hora_da_ligacao': '2019-05-07 18:43:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'SEM INTERESSE EM PAGAR', 'Dias_em_atraso_na_data_da_ligacao': 408}
{'_id': ObjectId('5d406cd0cdf51618d43b57d0'), 'ligacao_telefonica_ID': 49687, 'Numero_do_CPF': 87331667149, 'Data_hora_da_ligacao': '2019-05-07 18:43:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM CARNE', 'Dias_em_atraso_na_data_da_ligacao': 0}
{'_id': ObjectId('5d406cd0cdf51618d43b57d1'), 'ligacao_telefonica_ID': 49688, 'Numero_do_CPF': 10410639621, 'Data_hora_da_ligacao': '2019-05-07 18:43:00', 'Responsa

...

{'_id': ObjectId('5d406ceecdf51618d43bccb5'), 'ligacao_telefonica_ID': 79612, 'Numero_do_CPF': 11729647693, 'Data_hora_da_ligacao': '2019-05-28 19:01:00', 'Responsavel_pela_ligacao': 'COBRARR', 'Motivo_da_ligacao': 'REFERENCIA DESCONHECE O CLIENTE', 'Dias_em_atraso_na_data_da_ligacao': 791}
{'_id': ObjectId('5d406ceecdf51618d43bccb6'), 'ligacao_telefonica_ID': 79613, 'Numero_do_CPF': 13589994657, 'Data_hora_da_ligacao': '2019-05-28 19:01:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': 514}
{'_id': ObjectId('5d406ceecdf51618d43bccb7'), 'ligacao_telefonica_ID': 79614, 'Numero_do_CPF': 74437151615, 'Data_hora_da_ligacao': '2019-05-28 19:02:00', 'Responsavel_pela_ligacao': 'COBRARR', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': -9}
{'_id': ObjectId('5d406ceecdf51618d43bccb8'), 'ligacao_telefonica_ID': 79615, 'Numero_do_CPF': 46098593604, 'Data_hora_da_ligacao': '2019-05-28 19:02:00'

{'_id': ObjectId('5d406cefcdf51618d43bd021'), 'ligacao_telefonica_ID': 80488, 'Numero_do_CPF': 74146840678, 'Data_hora_da_ligacao': '2019-05-29 13:02:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': 433}
{'_id': ObjectId('5d406cefcdf51618d43bd022'), 'ligacao_telefonica_ID': 80489, 'Numero_do_CPF': 196491185, 'Data_hora_da_ligacao': '2019-05-29 13:02:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 68}
{'_id': ObjectId('5d406cefcdf51618d43bd023'), 'ligacao_telefonica_ID': 80490, 'Numero_do_CPF': 46516271615, 'Data_hora_da_ligacao': '2019-05-29 13:02:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 469}
{'_id': ObjectId('5d406cefcdf51618d43bd024'), 'ligacao_telefonica_ID': 80491, 'Numero_do_CPF': 58644733672, 'Data_hora_da_ligacao': '2019-05-29 13:02:00', 'Responsavel_pe

{'_id': ObjectId('5d406cf0cdf51618d43bd643'), 'ligacao_telefonica_ID': 82058, 'Numero_do_CPF': 7033691645, 'Data_hora_da_ligacao': '2019-05-29 21:33:00', 'Responsavel_pela_ligacao': 'COBRARR', 'Motivo_da_ligacao': 'INTERESSE EM PAGAR', 'Dias_em_atraso_na_data_da_ligacao': 168}
{'_id': ObjectId('5d406cf0cdf51618d43bd644'), 'ligacao_telefonica_ID': 82059, 'Numero_do_CPF': 80226612104, 'Data_hora_da_ligacao': '2019-05-29 21:33:00', 'Responsavel_pela_ligacao': 'COBRARR', 'Motivo_da_ligacao': 'SEM INTERESSE EM PAGAR', 'Dias_em_atraso_na_data_da_ligacao': 163}
{'_id': ObjectId('5d406cf0cdf51618d43bd645'), 'ligacao_telefonica_ID': 82060, 'Numero_do_CPF': 64960374691, 'Data_hora_da_ligacao': '2019-05-29 21:35:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'INTERESSE EM PAGAR', 'Dias_em_atraso_na_data_da_ligacao': 0}
{'_id': ObjectId('5d406cf0cdf51618d43bd646'), 'ligacao_telefonica_ID': 82061, 'Numero_do_CPF': 7251268680, 'Data_hora_da_ligacao': '2019-05-29 21:36:00', 'Respon

{'_id': ObjectId('5d406cf1cdf51618d43bd96d'), 'ligacao_telefonica_ID': 82868, 'Numero_do_CPF': 25257510197, 'Data_hora_da_ligacao': '2019-05-30 14:02:00', 'Responsavel_pela_ligacao': 'COBRARR', 'Motivo_da_ligacao': 'PROMESSA COM BOLETO', 'Dias_em_atraso_na_data_da_ligacao': -7}
{'_id': ObjectId('5d406cf1cdf51618d43bd96e'), 'ligacao_telefonica_ID': 82869, 'Numero_do_CPF': 1704607620, 'Data_hora_da_ligacao': '2019-05-30 14:02:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 670}
{'_id': ObjectId('5d406cf1cdf51618d43bd96f'), 'ligacao_telefonica_ID': 82870, 'Numero_do_CPF': 99644258134, 'Data_hora_da_ligacao': '2019-05-30 14:02:00', 'Responsavel_pela_ligacao': 'MAR AZUL', 'Motivo_da_ligacao': 'NÃ\x83O ATENDE', 'Dias_em_atraso_na_data_da_ligacao': 103}
{'_id': ObjectId('5d406cf1cdf51618d43bd970'), 'ligacao_telefonica_ID': 82871, 'Numero_do_CPF': 26435691134, 'Data_hora_da_ligacao': '2019-05-30 14:03:00', 'Responsavel_pe

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



# Registros de informacoes_adicionais

In [127]:
import pprint
db = client.cobrancas
informacoes_adicionais = db.informacoes_adicionais
cursor = informacoes_adicionais.find()
for document in cursor:
    pprint.pprint(document)

{'Responsaveis': 'Relatorio_de_acionamentos',
 'Responsaveis_ID': {'Aline Alves Luiz': 'Semear_1',
                     'Anna Paula Pereira Gomes': 'Semear_6',
                     'Bruno Naves de Oliveira': 'Semear_7',
                     'Daniele Cristiane de Freitas Duarte': 'Semear_8',
                     'Gabriel Torres de Carvalho Timochenco': 'Semear_3',
                     'Ingrid Pereira de Oliveira Silva': 'Semear_13',
                     'Leonardo Pereira Vida': 'Semear_0',
                     'Lourrane Carolina de Jesus Segala': 'Semear_4',
                     'Madson Gabriel Rocha Silva': 'Semear_9',
                     'Maria Fernanda Silva Pereira': 'Semear_5',
                     'Monaliza Nayanda Oliveira Rosa': 'Semear_10',
                     'Pollyane Nast cia Pereira de Jesus': 'Semear_12',
                     'Raiane Lorena Soares Oliveira': 'Semear_11',
                     'Richard Nunes de Sousa': 'Semear_2',
                     'Trissia Gabrielle Fe

In [120]:
db.cobrancas.informacoes_adicionais

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'cobrancas'), 'cobrancas.informacoes_adicionais')

# GERANDO KPIs

In [7]:
dados.head(3)

A o Agrupador                                   Nome  \
0  Contato telefÃ´nico    Semear             RIVALDO SANTOS DE MEDEIROS   
1  Contato telefÃ´nico    Semear  MARIA DOLORES RIBEIRO DA SILVA AMORIM   
2  Contato telefÃ´nico    Semear          SEBASTIAO WALDEMAR DOS SANTOS   

         Data Hor rio                            Respons vel   Motivo Contato  \
0  19/02/2019   12:46  Gabriel Torres de Carvalho Timochenco  CONTRA PROPOSTA   
1  19/02/2019   12:53  Gabriel Torres de Carvalho Timochenco  CONTRA PROPOSTA   
2  20/02/2019   13:18  Gabriel Torres de Carvalho Timochenco  CONTRA PROPOSTA   

      Situa o Dias atraso     Atual Saldo Total Saldo Cont bil    C digo  \
0  ConcluÃ­do         104    259,16      177,01              0   7208821   
1  ConcluÃ­do         315  2.605,44    1.165,47              0  10103672   
2  ConcluÃ­do         203  5.490,86    3.827,68              0  10391483   

      CPF CNPJ   Supervisor                              Agendador Assessoria  \
0  62361643120        ALINE  Gabriel Torres de Carvalho Timochenco        NaN   
1  97766330130     PATRICIA  Gabriel Torres de Carvalho Timochenco        NaN   
2  64756394604  MARIA LUIZA  Gabriel Torres de Carvalho Timochenco        NaN   

                                          Observa es Unnamed 18  
0  19/02/2019 - Proposta negada. Contra proposta ...        NaN  
1  Proposta para quitaÃ§Ã£o da parcela 08 aceita ...        NaN  
2  Proposta para quitaÃ§Ã£o da parcela 06 aceita ...        NaN

In [ ]:
dados.columns

In [22]:
len(set(collections.Counter(dados.loc[:,'C digo']).keys()))

31534

In [23]:
len(set(collections.Counter(dados.loc[:,'CPF CNPJ']).keys()))

31534

In [8]:
dados[dados.loc[:,'C digo'] == '9847454'].to_csv('exemplo_mesmo_codigo_acionamentos.csv',sep=';')

In [ ]:
dados[dados.loc[:,'CPF CNPJ'] == 7595238609]